# **Bancor Simulator - Demo & Tutorial**

<p align="center">
<img width="100%" src="https://d9hhrg4mnvzow.cloudfront.net/try.bancor.network/5edb37d6-open-graph-bancor3_1000000000000000000028.png" alt="bancor3" />
</p>

# Proposal: Limit on-curve liquidity to max(520 x 7 day fees, 100k BNT)

In the [Bancor Governance Forum](https://vote.bancor.network/), the BancorDAO (Decentralized Autonomous Organization) proposes and discusses token Whitelistings, Trading liquidity limits, Fee changes, Bancor Improvement Proposals, and others. To facilitate community participation, we have created this demo and tutorial notebook covering some relevant concepts for using the Bancor simulator for related analysis.

Please head on to the [Information and Templates](https://gov.bancor.network/c/information-and-templates/16) category for more information on the DAO process.

Voting happens on the [BancorDAO Snapshot Page](https://vote.bancor.network/).

The notebook presents an introduction to Bancor simulations, describing the structure and elements of the dataset(s), some relevant statistical properties, as well as running a baseline simulation and providing an example modified simulation model based on proposed changes discussed in **Proposal: Limit on-curve liquidity to max(520 x 7 day fees, 100k BNT)**.

## TLDR:

-   We pay IL on 100% of TKN available for trading
-   We get diminishing returns on new fees per unit of trading liquidity
-   If IL > fees then the protocol dies (and is already in crisis due to existing deficits)
-   B3 has the unique ability to set a cap on trading liquidity
-   Taking capital off-curve has a dual benefit of limiting IL exposure AND making it available to other revenue opportunities (native staking etc.)
-   Currently the protocol deficit increases when ETH price increases by ~1.5x annually relative to BNT, making some assumptions, we could lift this to the protocol being profitable up to a ~4x ETH annual moon relative to BNT by limiting the on-curve trading liquidity to 520x 7 day trading fees + implementing some modest staking model (or similar)
-   We should set a simple cap based on the data we have and commission a more sophisticated model in the near future

## Proposal:

When we look at the IL curve:

![image](https://aws1.discourse-cdn.com/standard20/uploads/bancordao/optimized/2X/e/e0d10c4f716b77cc23de68cb160db8c6e9dc28e1_2_690x387.png)


We see that the losses due to IL are a % of all the capital deployed on the trading curve.

If TKN moons 2x relative to BNT then the IL is ~10%, a 4x moon has ~20% IL, etc.

Meanwhile there are only so many fees due to trade volume across all of defi and almost all trades through bancor currently are based on arbitrage and aggregators only. That is to say, there is negligible trading being done directly on bancor due to retail etc. as that market is largely monopolized by aggregators and a few platforms that take the lion's share of human traders such as uniswap.

In considering this proposal, please consider mainly how **arb bots and aggregators** will respond, not human traders, as the former is 10x+ the latter in terms of protocol fee generation.

## Dataset description:

Datasets:
  * **[price_feeds.csv](https://bancorml.s3.us-east-2.amazonaws.com/price_feeds.csv)** - Dataset consists of token price feeds at daily resolution.
  * **[historical_actions.csv](https://bancorml.s3.us-east-2.amazonaws.com/historical_actions.csv)** - Dataset consists of Trade, Deposit, and Withdrawal actions performed on Bancor v3 since its launch in April.
  * **[fees_vs_liquidity.csv](https://bancorml.s3.us-east-2.amazonaws.com/fees_vs_liquidity.csv)** - Dataset consists of historical trading fees per token joined with on-curve liquidity snapshots.

**Bancor Simulator** is an open-source python package developed by **Bancor Research**. It aims to assist the design, testing, and validation of Bancor v3 tokenomics.

See [official documentation](https://simulator.bancor.network/chapters/bancor-simulator.html) for complete details.

In order to run the simulation software described herein, follow the setup and installation instructions below.

## Project setup

If you don't already have one, create a virtualenv
using [these instructions](https://docs.python.org/3/library/venv.html)

## Install

**Bancor Research** is available for Python 3.6+

To install using [pypi](https://pypi.org/project/bancor-simulation/), run this command:

````{tab} PyPI
$ pip install --upgrade bancor-research
````

Note, if running this command inside a jupyter notebook, use this instead:

````{tab} PyPI
$ ! pip install --upgrade bancor-research
````

In [0]:
%pip install bancor-research --force-reinstall

If you experience numpy related errors after installation, try reinstalling numpy as follows:

In [0]:
%pip install --upgrade numpy

Python interpreter will be restarted.
Requirement already satisfied: numpy in /local_disk0/.ephemeral_nfs/envs/pythonEnv-bd4fbddc-8193-4b62-851e-bda3f7b260a8/lib/python3.8/site-packages (1.23.2)
Python interpreter will be restarted.

Import the dependencies we will use.

In [0]:
from bancor_research import DEFAULT
import pandas as pd
import numpy as np
from datetime import datetime
from sklearn.utils import shuffle
from decimal import Decimal
import pprint
import plotly.express as px
from bancor_research.bancor_simulator.v3.spec import get_is_trading_enabled, get_bnt_funding_limit, get_vault_balance, \
    get_staked_balance, get_tkn_trading_liquidity, get_bnt_trading_liquidity, get_ema_rate, get_tkn_price

from typing import Tuple, Any

from bancor_research.bancor_simulator.v3.spec import get_prices, State, get_bnt_trading_liquidity, \
    get_tkn_trading_liquidity, get_trading_fee, get_user_balance, get_is_trading_enabled, get_network_fee, get_ema_rate, \
    get_spot_rate, get_vault_balance, get_pooltoken_balance, get_staked_balance, get_external_protection_vault, \
    get_protocol_wallet_balance, get_vortex_balance, get_bnt_funding_limit, get_bnbnt_rate, get_max_bnt_deposit, \
    get_user_pending_withdrawals, Token, get_bnt_min_liquidity, get_is_price_stable, get_pooltoken_name
from bancor_research.bancor_simulator.v3.spec.actions import (
    unpack_withdrawal_cooldown,
    vortex_burner,
)
from bancor_research.bancor_simulator.v3.spec.network import BancorDapp
from bancor_research.bancor_simulator.v3.spec.utils import (
    compute_user_total_holdings,
    compute_ema,
    compute_bntkn_rate,
    compute_max_tkn_deposit,
    compute_vault_tkn_tvl, check_pool_shutdown, shutdown_pool,
)
import random

/databricks/python/lib/python3.8/site-packages/scipy/__init__.py:138: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.2)
 warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion} is required for this version of "

Define the constants we will use:

In [0]:
default_trading_fee = '1%'
default_bnt_funding_limit = 1000000
target_tvl = Decimal("160000000")
pool_freq_dist = {}
whitelisted_tokens = {}
action_freq_dist = {}
historical_action_distribution_dic = {}
arbitrage_percentage = .99
bnt_min_liquidity = 20000
constant_multiplier = 520
n_periods = 7
price_feeds_path = 'https://bancorml.s3.us-east-2.amazonaws.com/price_feeds.csv'
historical_actions_path = 'https://bancorml.s3.us-east-2.amazonaws.com/historical_actions.csv'
fees_vs_liquidity_path = 'https://bancorml.s3.us-east-2.amazonaws.com/fees_vs_liquidity.csv'
global_username = 'global user'

## Loading the data

Load the price feed data:

In [0]:
price_feeds = pd.read_csv(price_feeds_path)

for n in range(10):
    price_feeds = shuffle(price_feeds)
    
price_feeds['indx'] = [i for i in range(len(price_feeds))]
price_feeds

Out[3]:

indx 
 bat 
 bnt 
 dai 
 enj 
 link 
 mana 
 matic 
 mkr 
 mln 
 ocean 
 omg 
 ren 
 rsr 
 usdc 
 usdt 
 wbtc 
 eth 
 
 
 
 
 277931 
 0 
 0.212999 
 0.271057 
 1.009967 
 0.104666 
 3.94 
 0.038469 
 0.019682 
 542.00 
 4.19 
 0.052621 
 0.854450 
 0.057461 
 0.004916 
 1.002364 
 1.003195 
 8652.40 
 221.68 
 
 
 361227 
 1 
 0.184797 
 0.207026 
 1.019513 
 0.139200 
 3.70 
 0.032581 
 0.015749 
 337.76 
 3.16 
 0.067179 
 0.671549 
 0.066189 
 0.002559 
 1.007159 
 1.009262 
 7801.03 
 198.71 
 
 
 1002946 
 2 
 0.522566 
 2.790000 
 1.000012 
 1.185356 
 15.32 
 0.611471 
 0.808896 
 2425.35 
 75.52 
 0.380075 
 3.640000 
 0.308084 
 0.019636 
 1.002210 
 1.002624 
 31440.74 
 1898.21 
 
 
 739159 
 3 
 0.272144 
 1.830000 
 1.000962 
 0.194811 
 21.87 
 0.112034 
 0.035715 
 1529.72 
 39.10 
 0.552180 
 3.780000 
 0.541203 
 0.043662 
 0.999693 
 1.001874 
 37537.03 
 1218.09 
 
 
 245318 
 4 
 0.258387 
 0.322548 
 1.003189 
 0.127111 
 3.31 
 0.055444 
 0.021705 
 573.13 
 5.57 
 0.058898 
 1.148919 
 0.061432 
 0.002079 
 1.003305 
 1.003599 
 9892.99 
 226.09 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 594758 
 1052506 
 0.211326 
 1.055217 
 1.004783 
 0.143758 
 8.72 
 0.071491 
 0.016547 
 510.72 
 22.54 
 0.312236 
 3.160000 
 0.259497 
 0.008217 
 1.000989 
 1.001942 
 10629.97 
 339.50 
 
 
 318695 
 1052507 
 0.140203 
 0.172217 
 1.022994 
 0.087858 
 2.17 
 0.025192 
 0.010843 
 304.49 
 2.73 
 0.047483 
 0.506710 
 0.042370 
 0.002307 
 1.001896 
 1.003651 
 6334.27 
 133.35 
 
 
 91664 
 1052508 
 0.238393 
 0.309421 
 1.013647 
 0.058911 
 2.73 
 0.027702 
 0.013613 
 458.83 
 3.44 
 0.020860 
 0.794323 
 0.054162 
 0.001831 
 1.005404 
 1.009506 
 7483.82 
 162.64 
 
 
 30705 
 1052509 
 0.174421 
 0.366104 
 1.018336 
 0.071138 
 1.74 
 0.031402 
 0.012884 
 464.20 
 4.35 
 0.021603 
 1.041419 
 0.040797 
 0.002393 
 1.004096 
 1.004667 
 10200.80 
 179.19 
 
 
 187079 
 1052510 
 0.190663 
 0.271992 
 1.002843 
 0.081562 
 1.89 
 0.033000 
 0.014919 
 445.65 
 3.11 
 0.030388 
 0.639380 
 0.031319 
 0.001387 
 1.005214 
 1.003948 
 7378.16 
 134.81 
 
 
 
 1052511 rows × 18 columns

Load the historical actions data:

In [0]:
historical_actions = pd.read_csv(historical_actions_path)
historical_actions

Out[4]:

user_id 
 blocknumber 
 time 
 timestamp 
 poolSymbol 
 tokenAmount_real 
 tokenAmount_real_usd 
 targetSymbol 
 event_name 
 
 
 
 
 0 
 0xb0B958398ABB0b5DB4ce4d7598Fb868f5A00f372 
 14611842 
 2022-04-18 22:38:30+00:00 
 1650321510 
 eth 
 NaN 
 NaN 
 NaN 
 deposit 
 
 
 1 
 0xb0B958398ABB0b5DB4ce4d7598Fb868f5A00f372 
 14611854 
 2022-04-18 22:40:44+00:00 
 1650321644 
 eth 
 NaN 
 NaN 
 NaN 
 deposit 
 
 
 2 
 0xb0B958398ABB0b5DB4ce4d7598Fb868f5A00f372 
 14611870 
 2022-04-18 22:43:01+00:00 
 1650321781 
 dai 
 NaN 
 NaN 
 NaN 
 deposit 
 
 
 3 
 0xb0B958398ABB0b5DB4ce4d7598Fb868f5A00f372 
 14611880 
 2022-04-18 22:45:09+00:00 
 1650321909 
 dai 
 NaN 
 NaN 
 NaN 
 deposit 
 
 
 4 
 0xb0B958398ABB0b5DB4ce4d7598Fb868f5A00f372 
 14611897 
 2022-04-18 22:49:18+00:00 
 1650322158 
 eth 
 NaN 
 NaN 
 NaN 
 deposit 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 39855 
 0x7e84638EfcF13bb710D591048532AB09990B7c4a 
 15304180 
 2022-08-08 22:11:43+00:00 
 1659996703 
 psp 
 8007.191743 
 0.000000 
 NaN 
 deposit 
 
 
 39856 
 0x7e84638EfcF13bb710D591048532AB09990B7c4a 
 15304199 
 2022-08-08 22:15:42+00:00 
 1659996942 
 psp 
 8007.191743 
 0.000000 
 NaN 
 withdraw_initiated 
 
 
 39857 
 0x7e84638EfcF13bb710D591048532AB09990B7c4a 
 15304206 
 2022-08-08 22:16:36+00:00 
 1659996996 
 psp 
 8007.191743 
 0.000000 
 NaN 
 withdraw_completed 
 
 
 39858 
 0xf3Db3e79cD7dd756d4BABAC4B7D64003fe4B33fA 
 15304602 
 2022-08-08 23:40:06+00:00 
 1660002006 
 link 
 234.392076 
 1945.021066 
 NaN 
 withdraw_initiated 
 
 
 39859 
 0xf3Db3e79cD7dd756d4BABAC4B7D64003fe4B33fA 
 15304607 
 2022-08-08 23:40:53+00:00 
 1660002053 
 link 
 234.392076 
 1945.021066 
 NaN 
 withdraw_completed 
 
 
 
 39860 rows × 9 columns

Load the fees vs liquidity data and do some preprocessing:

In [0]:
fees_vs_liquidity = pd.read_csv(fees_vs_liquidity_path).drop('Unnamed: 0', axis=1)
fees_vs_liquidity['tknTradingLiquidity_real_bnt'] = fees_vs_liquidity['tknTradingLiquidity_real'] * fees_vs_liquidity['price']

Find which tokens are included in all three datasets (we will focus on these in our simulations):

In [0]:
price_feed_tokens = price_feeds.T.reset_index().rename({'index':'tkn_name'}, axis=1)['tkn_name'].unique()
simulation_tokens = [tkn for tkn in historical_actions['poolSymbol'].unique() if tkn in price_feed_tokens]
print(simulation_tokens)

['eth', 'dai', 'link', 'bnt', 'bat', 'usdc', 'ren', 'wbtc', 'enj', 'mkr', 'matic', 'mana', 'mln', 'usdt', 'ocean', 'omg']

Filter the actions to include only those we have price and liquidity data for:

In [0]:
historical_actions = historical_actions[historical_actions['poolSymbol'].isin(simulation_tokens)]

Get the distribution of historical actions:

In [0]:
c = historical_actions.event_name.value_counts(dropna=False)
p = historical_actions.event_name.value_counts(dropna=False, normalize=True)
historical_action_distribution = pd.concat([c,p], axis=1, keys=['counts', '%'])
historical_action_distribution

Out[8]:

counts 
 % 
 
 
 
 
 trade 
 14573 
 0.438325 
 
 
 deposit 
 10924 
 0.328571 
 
 
 withdraw_initiated 
 3875 
 0.116552 
 
 
 withdraw_completed 
 2503 
 0.075285 
 
 
 withdraw_canceled 
 707 
 0.021265 
 
 
 withdraw_pending 
 665 
 0.020002

Get the distribution of all historical actions by token:

In [0]:
c = historical_actions.poolSymbol.value_counts(dropna=False)
p = historical_actions.poolSymbol.value_counts(dropna=False, normalize=True)
historical_action_tkn_distribution = pd.concat([c,p], axis=1, keys=['counts', '%'])
historical_action_tkn_distribution

Out[9]:

counts 
 % 
 
 
 
 
 bnt 
 14577 
 0.438446 
 
 
 eth 
 8140 
 0.244834 
 
 
 link 
 5919 
 0.178031 
 
 
 dai 
 1837 
 0.055253 
 
 
 wbtc 
 750 
 0.022558 
 
 
 enj 
 503 
 0.015129 
 
 
 usdc 
 501 
 0.015069 
 
 
 matic 
 281 
 0.008452 
 
 
 bat 
 160 
 0.004812 
 
 
 usdt 
 142 
 0.004271 
 
 
 ocean 
 130 
 0.003910 
 
 
 ren 
 129 
 0.003880 
 
 
 mana 
 89 
 0.002677 
 
 
 mkr 
 72 
 0.002166 
 
 
 mln 
 11 
 0.000331 
 
 
 omg 
 6 
 0.000180

We can solve for a reasonable starting balance per token for a single global user as described in detail below.

In [0]:
user_initial_balances = historical_actions
user_initial_balances['user_id'] = [global_username for _ in range(len(user_initial_balances))]
user_initial_balances = historical_actions[
    ['user_id','poolSymbol','tokenAmount_real_usd']].groupby(['user_id','poolSymbol']).sum()
user_initial_balances = user_initial_balances.reset_index()
user_initial_balances = user_initial_balances[user_initial_balances['poolSymbol'].isin(simulation_tokens)]
user_initial_balances = user_initial_balances[user_initial_balances['tokenAmount_real_usd'] > 0]
user_initial_balances

<command-526051424433796>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
 user_initial_balances['user_id'] = [global_username for _ in range(len(user_initial_balances))]
Out[10]:

user_id 
 poolSymbol 
 tokenAmount_real_usd 
 
 
 
 
 0 
 global user 
 bat 
 1.802011e+06 
 
 
 1 
 global user 
 bnt 
 2.333260e+08 
 
 
 2 
 global user 
 dai 
 1.339821e+08 
 
 
 3 
 global user 
 enj 
 6.652445e+06 
 
 
 4 
 global user 
 eth 
 4.025186e+08 
 
 
 5 
 global user 
 link 
 1.811982e+08 
 
 
 6 
 global user 
 mana 
 9.275342e+05 
 
 
 7 
 global user 
 matic 
 1.625861e+06 
 
 
 8 
 global user 
 mkr 
 2.038746e+06 
 
 
 10 
 global user 
 ocean 
 3.230327e+05 
 
 
 12 
 global user 
 ren 
 3.620459e+05 
 
 
 13 
 global user 
 usdc 
 1.445411e+07 
 
 
 14 
 global user 
 usdt 
 5.855184e+06 
 
 
 15 
 global user 
 wbtc 
 4.160234e+07

## `MonteCarloGenerator` Simulation Setup

In [0]:
h = historical_action_distribution.reset_index()
h

Out[11]:

index 
 counts 
 % 
 
 
 
 
 0 
 trade 
 14573 
 0.438325 
 
 
 1 
 deposit 
 10924 
 0.328571 
 
 
 2 
 withdraw_initiated 
 3875 
 0.116552 
 
 
 3 
 withdraw_completed 
 2503 
 0.075285 
 
 
 4 
 withdraw_canceled 
 707 
 0.021265 
 
 
 5 
 withdraw_pending 
 665 
 0.020002

Create the `action_freq_dist` which tells the simulator how often it should randomly generate specific actions (e.g. trades, deposits, etc...). You can either manually specify these amounts, or use a data-based approach like we use here:

In [0]:
a = historical_action_distribution.reset_index()
all_actions = h['index'].unique()
for action in all_actions:
    action_freq_dist[action] = a[a['index']==action]['%'].values[0]
    
# Prints formatted action_freq_dist dictionary
pprint.pprint(action_freq_dist)

{'deposit': 0.32857099888711766,
 'trade': 0.4383252624296929,
 'withdraw_canceled': 0.021265076548259994,
 'withdraw_completed': 0.0752849881192288,
 'withdraw_initiated': 0.11655186934159473,
 'withdraw_pending': 0.020001804674105936}

Create the `pool_freq_dist` which tells the simulator how often it should randomly select specific pools (e.g. ETH, DAI, etc...) when performing an action. You can either manually specify this, or use a data-based approach like we use here. Note that in the loop below we're also building the `whitelisted_tokens` parameter which tells the simulator which pools to use as well as their initial `trading_fee` and `bnt_funding_limit` parameters.

In [0]:
d = historical_action_tkn_distribution.reset_index()
for tkn in simulation_tokens:
    pool_freq_dist[tkn] = d[d['index']==tkn]['%'].values[0]
    whitelisted_tokens[tkn] = {'trading_fee': default_trading_fee, 'bnt_funding_limit': default_bnt_funding_limit}
    
# Prints formatted pool_freq_dist dictionary
pprint.pprint(pool_freq_dist)

{'bat': 0.004812464282491653,
 'bnt': 0.4384455740367552,
 'dai': 0.05525310554335729,
 'enj': 0.015129184588083135,
 'eth': 0.24483412037176286,
 'link': 0.1780311005504256,
 'mana': 0.002676933257135982,
 'matic': 0.008451890396125965,
 'mkr': 0.002165608927121244,
 'mln': 0.00033085691942130117,
 'ocean': 0.003910127229524468,
 'omg': 0.000180467410593437,
 'ren': 0.0038800493277588955,
 'usdc': 0.01506902878455199,
 'usdt': 0.004271062050711342,
 'wbtc': 0.022558426324179624}

Print the formatted `whitelisted_tokens` dictionary for reference.

In [0]:
pprint.pprint(whitelisted_tokens)

{'bat': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'bnt': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'dai': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'enj': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'eth': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'link': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'mana': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'matic': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'mkr': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'mln': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'ocean': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'omg': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'ren': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'usdc': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'usdt': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'},
 'wbtc': {'bnt_funding_limit': 1000000, 'trading_fee': '1%'}}

We can solve for the average number of events per day `mean_events_per_day`. This will tell us how often we should update the `bnt_funding_limit` parameter. Note: you can manually override this value to speed-up the simulation.

In [0]:
from datetime import datetime

date_time_str = '01/07/22 00:00:00'
date_time_obj = datetime.strptime(date_time_str, '%d/%m/%y %H:%M:%S')
time = historical_actions.copy()
time['date'] = [datetime.strptime(str(i), '%Y-%m-%d') for i in pd.to_datetime(time['time']).dt.date.values]
time = time[time['date'] > date_time_obj]
mean_events_per_day = time.groupby('date').count()['event_name'].mean()

# mean_events_per_day = 50
print(f'mean_events_per_day={mean_events_per_day}')

mean_events_per_day=231.6315789473684

Below we set the `num_simulation_days` parameter in order to tell the simulator how long we want to run the simulation. The units of this are in `days` in order to allow us to convert the proposal's `rolling 7 day average trade fees` into some number of simulated actions.

Note that the simulator uses `timestamps` throughout the codebase. In the current simulation, every timestamp iteration corresponds to 1 action.

The `simulation_step_count` specifies the number of sequential actions we will simulate. By our definitions above, this number of actions we would expect to see over a time period of `180 days` based on the average number of actions per day.

In [0]:
num_simulation_days = 30
num_timestamps_per_day = 60 * 24 # minutes / day (same resolution as price feeds)
num_timesteps = num_simulation_days * num_timestamps_per_day
assert len(price_feeds) > num_timesteps, "the number of timesteps must be less than the length of the price feeds table"
simulation_actions_count = int(round(mean_events_per_day * num_simulation_days, 0))

print(simulation_actions_count, num_timesteps)

6949 43200

The `transact(...)` function below is the main logic which specifies the Monte-Carlo transaction (deposit, trade, etc...) frequency distributions.

In [0]:
def transact(self, is_proposal):
    self.latest_amt = None
    self.latest_tkn_name = None
    self.user_name = global_username

    latest_action = None
    timestamp = self.timestamp
    
    i = self.random.randint(0, self.num_timesteps)
    
    deposit_range = self.simulation_actions_count * self.action_freq_dist['deposit']
    trade_range = deposit_range + self.simulation_actions_count * self.action_freq_dist['trade'] * (1 - arbitrage_percentage)
    arb_range = trade_range + self.simulation_actions_count * self.action_freq_dist['trade'] * arbitrage_percentage
    withdraw_initiated = arb_range + self.simulation_actions_count * self.action_freq_dist['withdraw_initiated']
    withdraw_completed = withdraw_initiated + self.simulation_actions_count * self.action_freq_dist['withdraw_completed']
    withdraw_canceled = withdraw_completed + self.simulation_actions_count * self.action_freq_dist['withdraw_canceled']
    withdraw_pending = withdraw_canceled + self.simulation_actions_count * self.action_freq_dist['withdraw_pending']

    if i < deposit_range:
        latest_action = "deposit"
        self.perform_random_deposit()

    elif deposit_range <= i < trade_range:
        latest_action = "trade"
        self.perform_random_trade()

    elif trade_range <= i < arb_range:
        latest_action = "arbitrage_trade"
        self.perform_random_arbitrage_trade()

    elif arb_range <= i < withdraw_initiated:
        latest_action = "cooldown"
        self.perform_random_begin_cooldown()

    elif withdraw_initiated <= i < withdraw_completed:
        latest_action = "withdrawal"
        self.perform_random_withdrawal()
        
    else:
        latest_action = "skip"
    
    if latest_action != 'skip':
        state = self.protocol.global_state
        state.timestamp = timestamp
        for tkn_name in self.whitelisted_tokens:
            if not get_is_trading_enabled(state, tkn_name):
                self.protocol.enable_trading(tkn_name=tkn_name, timestamp=timestamp)

        # The code below creates a new dataframe which collects the data we want to analyze about the simulation.
        df = {}
        df['timestamp'] = [timestamp]
        df['latest_action'] = [latest_action]
        df['latest_amt'] = [self.latest_amt]
        df['latest_tkn_name'] = [self.latest_tkn_name]
        total_def = Decimal('0')
        total_def_bnt = Decimal('0')
        total_def_usd = Decimal('0')

        for tkn in self.whitelisted_tokens:
            if tkn != 'bnt':
                ema_rate = get_ema_rate(state, tkn)
                bntprice = get_tkn_price(state, 'bnt')
                df[f'{tkn}_bnt_funding_limit'] = [get_bnt_funding_limit(state, tkn)]
                df[f'{tkn}_vault'] = [get_vault_balance(state, tkn)]
                df[f'{tkn}_staking'] = [get_staked_balance(state, tkn)]
                df[f'{tkn}_surplus'] = [df[f'{tkn}_vault'][0] - df[f'{tkn}_staking'][0]]
                df[f'{tkn}_surplus_bnt'] = [df[f'{tkn}_surplus'][0] * ema_rate]
                df[f'{tkn}_surplus_usd'] = [df[f'{tkn}_surplus_bnt'][0] * bntprice]
                total_def += df[f'{tkn}_surplus'][0]
                total_def_bnt += df[f'{tkn}_surplus_bnt'][0]
                total_def_usd += df[f'{tkn}_surplus_usd'][0]
                df[f'{tkn}_tkn_trading_liquidity'] = [get_tkn_trading_liquidity(state, tkn)]
                df[f'{tkn}_bnt_trading_liquidity'] = [get_bnt_trading_liquidity(state, tkn)]

        df[f'total_surplus'] = [total_def]
        df[f'total_surplus_bnt'] = [total_def_bnt]
        df[f'total_surplus_usd'] = [total_def_usd]
        df = pd.DataFrame(df)
        self.logger.append(df)

Next we define a few helper functions which allow us to simulate specific actions.

In [0]:
def trade_tkn_to_ema(
        bnt_trading_liquidity: Decimal,
        tkn_trading_liquidity: Decimal,
        trading_fee: Decimal,
        network_fee: Decimal,
        future_ema: Decimal,
) -> Decimal:
    """
    Outputs the tkn_amt that should be traded to force the ema and the spot price together on a given pool.
    """
    a = bnt_trading_liquidity
    b = tkn_trading_liquidity
    d = trading_fee
    e = network_fee
    f = future_ema
    tkn_amt = (
                      (a * d * (Decimal("1") - e) - Decimal("2") * f * b)
                      + (
                              a
                              * (
                                      Decimal("4") * f * b * (Decimal("1") - d * (Decimal("1") - e))
                                      + a * d ** Decimal("2") * (Decimal("1") - e) ** Decimal("2")
                              )
                      )
                      ** (Decimal("1") / Decimal("2"))
              ) / (Decimal("2") * f)
    return tkn_amt



def trade_bnt_to_ema(
        bnt_trading_liquidity,
        tkn_trading_liquidity,
        trading_fee,
        network_fee,
        future_ema,
):
    """
    Analyze the state of any pool and create a swap that drives the ema and the spot price together.
    """

    a = bnt_trading_liquidity
    b = tkn_trading_liquidity
    d = trading_fee
    e = network_fee
    f = future_ema
    x = (
                -Decimal("2") * a
                + b * d * f
                + (
                        (Decimal("2") * a - b * d * f) ** Decimal("2")
                        - Decimal("4") * a * (a - b * f)
                )
                ** (Decimal("1") / Decimal("2"))
        ) / Decimal("2")
    a_recursion = (
                          a * (a + x) + d * (Decimal("1") - e) * (a * x + x ** Decimal("2"))
                  ) / (a + d * x)
    b_recursion = b * (a + d * x) / (a + x)
    n = 0
    p = Decimal("0.001")
    while a_recursion / b_recursion < f:
        n += 1
        p += Decimal("0.0001")
        x += x * (f ** p - (a_recursion / b_recursion) ** p) / f
        a_recursion = (
                              a * (a + x) + d * (Decimal("1") - e) * (a * x + x ** Decimal("2"))
                      ) / (a + d * x)
        b_recursion = b * (a + d * x) / (a + x)
        if n > 20000:
            break
    bnt_amt = x
    return bnt_amt

def process_arbitrage_trade(
        tkn_name: str,
        tkn_token_virtual_balance: Decimal,
        bnt_virtual_balance: Decimal,
        bnt_trading_liquidity: Decimal,
        tkn_trading_liquidity: Decimal,
        trading_fee: Decimal,
        user_tkn: Decimal,
        user_bnt: Decimal,
) -> Tuple[Decimal, str, str, bool]:
    """
    Computes the appropriate arbitrage trade on the tkn_name pool.
    """
    a = bnt_trading_liquidity
    b = tkn_trading_liquidity
    m = trading_fee
    p = bnt_virtual_balance
    q = tkn_token_virtual_balance

    bnt_trade_amt = (
                            -Decimal("2") * a * q
                            + b * m * p
                            + (
                                    (Decimal("2") * a * q - b * m * p) ** Decimal("2")
                                    - Decimal("4") * a * q * (a * q - b * p)
                            )
                            ** (Decimal("1") / Decimal("2"))
                    ) / (Decimal("2") * q)

    tkn_trade_amt = (
                            -Decimal("2") * b * p
                            + a * m * q
                            + (
                                    (Decimal("2") * b * p - a * m * q) ** Decimal("2")
                                    - Decimal("4") * b * p * (b * p - a * q)
                            )
                            ** (Decimal("1") / Decimal("2"))
                    ) / (Decimal("2") * p)

    if bnt_trade_amt > 0:
        source_token = "bnt"
        target_token = tkn_name
        trade_amt = bnt_trade_amt
        user_capability = user_bnt > bnt_trade_amt
        return trade_amt, source_token, target_token, user_capability

    elif tkn_trade_amt > 0:
        source_token = tkn_name
        target_token = "bnt"
        trade_amt = tkn_trade_amt
        user_capability = user_tkn > tkn_trade_amt
        return trade_amt, source_token, target_token, user_capability

Finally, we define the main logical class `MonteCarloGenerator` which we will use to run our simulation.

In [0]:
class MonteCarloGenerator(object):
    """
    Generates Monte Carlo scenarios.
    """

    def __init__(
            self,
            target_tvl: Decimal,
            whitelisted_tokens: dict,
            price_feed: pd.DataFrame,
            user_initial_balances: pd.DataFrame,
            simulation_actions_count: int,
            num_timesteps: int,
            pool_freq_dist: dict,
            action_freq_dist: dict,
            bnt_min_liquidity: Any = 10000,
            
    ):

        # all users/agents use a single BancorDapp instance
        v3 = BancorDapp(whitelisted_tokens=whitelisted_tokens,
                        bnt_min_liquidity=bnt_min_liquidity,
                        price_feeds=price_feed)

        # set the initial balances for each user.
        for user_id in user_initial_balances['user_id'].unique():
            v3.create_user(user_id)

            user_balances = user_initial_balances[user_initial_balances['user_id'] == user_id]
            for tkn_name in user_balances['poolSymbol'].unique():

                user_balance = user_balances[user_balances['poolSymbol'] == tkn_name]['tokenAmount_real_usd'].values[0]
                v3.set_user_balance(user_name=user_id, tkn_name=tkn_name, tkn_amt=user_balance, timestamp=0)

                pooltkn_name = get_pooltoken_name(tkn_name)
                if pooltkn_name not in v3.global_state.users[user_id].wallet:
                    v3.global_state.users[user_id].wallet[pooltkn_name] = Token(
                        balance=Decimal('0')
                    )

        self.protocol = v3
        self.random = random
        self.logger = []
        self.timestamp = 0
        self.target_tvl = target_tvl
        self.simulation_actions_count = simulation_actions_count
        self.whitelisted_tokens = whitelisted_tokens
        self.daily_trade_volume = 0
        self.latest_amt = 0
        self.latest_tkn_name = None
        self.rolling_trade_fees = {}
        self.action_freq_dist = action_freq_dist
        self.num_timesteps = num_timesteps

        random_tkn_names = []
        
        # create a list of tokens which occur at the desired frequency
        for tkn in pool_freq_dist:
            self.rolling_trade_fees[tkn] = []
            freq = int(round(float(pool_freq_dist[tkn] * simulation_actions_count), 0))
            for i in range(freq):
                random_tkn_names.append(tkn)

        # randomly shuffle the list of tokens that we will select from
        random.seed(1)
        for i in range(50):
            random.shuffle(random_tkn_names)
        self.pool_freq_dist_list = random_tkn_names

    def get_random_amt(self, amt: Decimal) -> Decimal:
        if self.random.randint(0, 1000) != 0:
            max_amt, min_amt = amt * Decimal("0.0001"), amt * Decimal("0.000001")
        else:
            max_amt, min_amt = amt * Decimal("0.01"), amt * Decimal("0.001")
        return Decimal(self.random.uniform(float(min_amt), float(max_amt)))

    def perform_random_trade(self):
        """
        Performs a random trade on the server.
        """
        state = self.protocol.global_state
        timestamp = self.timestamp
        user_name = self.user_name
        tkn_name, target_tkn = self.get_random_tkn_names(state)
        source_liquidity = get_tkn_trading_liquidity(state, tkn_name)
        bnt_min_liquidity = get_bnt_min_liquidity(state, tkn_name)
        bnt_trading_liquidity = get_bnt_trading_liquidity(state, tkn_name)
        delta = bnt_trading_liquidity - bnt_min_liquidity
        user_funds = get_user_balance(state, user_name, tkn_name)
        is_trading_enabled_source = get_is_trading_enabled(state, tkn_name)
        is_trading_enabled_target = get_is_trading_enabled(state, target_tkn)
        amt = 0
#         if is_trading_enabled_source and is_trading_enabled_target:
        swap_amt = self.get_random_amt(source_liquidity)
        if pd.isnull(user_funds):
            user_funds = Decimal('0')

        if pd.isnull(swap_amt):
            swap_amt = Decimal('0')
        if user_funds > swap_amt:
            amt = swap_amt
        else:
            amt = user_funds

        if amt > 0:
            self.protocol.trade(
                tkn_amt=amt,
                source_token=tkn_name,
                target_token=target_tkn,
                user_name=user_name,
                timestamp=timestamp,
            )
        if target_tkn == 'bnt':
            tkn = tkn_name
        else:
            tkn = target_tkn
        trading_fee = get_trading_fee(state, tkn)
        fees_earned = trading_fee * amt
        if fees_earned > 0:
            self.rolling_trade_fees[tkn].append(fees_earned)
        self.daily_trade_volume += amt
        self.latest_tkn_name = tkn_name + "_" + target_tkn
        self.latest_amt = amt
        return self

    def arbitrage_trade(self, state: State, tkn_name: str, target_tkn: str, user_name: str):
        """
        Computes the appropriate arbitrage trade on the tkn_name pool.
        """
        timestamp = self.timestamp
        tkn_price, bnt_price = get_prices(state, tkn_name)
        bnt_trading_liquidity = get_bnt_trading_liquidity(state, tkn_name)
        tkn_trading_liquidity = get_tkn_trading_liquidity(state, tkn_name)
        trading_fee = get_trading_fee(state, tkn_name)
        user_tkn = get_user_balance(state, user_name, tkn_name)
        user_bnt = get_user_balance(state, user_name, "bnt")
        is_trading_enabled_source = get_is_trading_enabled(state, tkn_name)
        is_trading_enabled_target = get_is_trading_enabled(state, target_tkn)
        trade_amt = Decimal('0')
        source_token = tkn_name
        target_token = target_tkn
#         if is_trading_enabled_source and is_trading_enabled_target:
        x = process_arbitrage_trade(
            tkn_name,
            tkn_price,
            bnt_price,
            bnt_trading_liquidity,
            tkn_trading_liquidity,
            trading_fee,
            user_tkn,
            user_bnt,
        )
        if x is not None:
            (
                trade_amt,
                source_token,
                target_token,
                user_capability,
            ) = x
            if user_capability:
                if trade_amt > 0:
                    self.protocol.trade(
                        trade_amt, source_token, target_token, user_name, timestamp
                    )
        self.daily_trade_volume += trade_amt
        self.latest_tkn_name = source_token + "_" + target_token
        self.latest_amt = trade_amt
        if target_token == 'bnt':
            tkn = source_token
        else:
            tkn = target_token
        trading_fee = get_trading_fee(state, tkn)
        fees_earned = trading_fee * trade_amt
        if fees_earned > 0:
            self.rolling_trade_fees[tkn].append(fees_earned)

    def perform_random_arbitrage_trade(self):
        """
        Performs a random arbitrage trade.
        """
        state = self.protocol.global_state
        user_name = self.random.choice([usr for usr in state.users if usr != 'protocol'])
        tkn_name, target_tkn = self.get_random_tkn_names(state)
        self.arbitrage_trade(state, tkn_name, target_tkn, user_name)
        return self

    def process_force_moving_average(
            self, tkn_name: str, user_tkn: Decimal, user_bnt: Decimal
    ) -> Tuple[Decimal, str, str, bool]:
        """
        Process the trade amount to force the ema and the spot price together.
        """
        state = self.protocol.global_state
        tkn_trading_liquidity = get_tkn_trading_liquidity(state, tkn_name)
        bnt_trading_liquidity = get_bnt_trading_liquidity(state, tkn_name)
        trading_fee = get_trading_fee(state, tkn_name)
        network_fee = get_network_fee(state, tkn_name)
        ema_rate = get_ema_rate(state, tkn_name)
        spot_rate = get_spot_rate(state, tkn_name)
        future_ema = compute_ema(spot_rate, ema_rate)
        if ema_rate < spot_rate:
            source_tkn = tkn_name
            target_tkn = "bnt"
            trade_amt = trade_tkn_to_ema(
                bnt_trading_liquidity,
                tkn_trading_liquidity,
                trading_fee,
                network_fee,
                future_ema,
            )
            user_capability = user_tkn > trade_amt
        elif ema_rate > spot_rate:
            source_tkn = "bnt"
            target_tkn = tkn_name
            trade_amt = trade_bnt_to_ema(
                bnt_trading_liquidity,
                tkn_trading_liquidity,
                trading_fee,
                network_fee,
                future_ema,
            )
            user_capability = user_bnt > trade_amt
        else:
            source_tkn = tkn_name
            target_tkn = tkn_name
            trade_amt = Decimal("0")
            user_capability = False
        self.latest_tkn_name = source_tkn + "_" + target_tkn
        self.latest_amt = trade_amt
        return trade_amt, source_tkn, target_tkn, user_capability

    def force_moving_average(
            self, state: State, tkn_name: str, user_name: str, timestamp: int
    ):
        """
        Analyze the state of a pool and creates a swap that drives the ema and the spot price together.
        """
        user_tkn = get_user_balance(state, user_name, tkn_name)
        user_bnt = get_user_balance(state, user_name, "bnt")
        if get_is_trading_enabled(state, tkn_name):
            (
                tkn_amt,
                source_token,
                target_token,
                user_capability,
            ) = self.process_force_moving_average(tkn_name, user_tkn, user_bnt)
            if user_capability:
                self.protocol.trade(
                    tkn_amt, source_token, target_token, user_name, timestamp
                )
                self.daily_trade_volume += tkn_amt
                self.latest_tkn_name = source_token + "_" + target_token
                self.latest_amt = tkn_amt
        return self

    def perform_random_ema_force_trade(self):
        state = self.protocol.global_state
        timestamp = self.timestamp
        user_name = self.random.choice(state.usernames)
        tokens = [token for token in state.whitelisted_tokens if token != "bnt"]
        tkn_name = self.random.choice(tokens)
        if get_is_trading_enabled(state, tkn_name):
            self.force_moving_average(state, tkn_name, user_name, timestamp)
        return self

    def get_random_tkn_names(self, state: State) -> Tuple[str, str]:
        source_tkn, target_tkn = 'None', 'None'
        while source_tkn == target_tkn:
            source_tkn, target_tkn = self.random.sample(self.pool_freq_dist_list, 2)
        if source_tkn == target_tkn:
            target_tkn  = self.random.sample(self.pool_freq_dist_list.remove(source_tkn), 1)
        return source_tkn, target_tkn

    def get_average_trading_fee(self):
        state = self.protocol.global_state
        return np.average(
            [
                float(state.tokens[tkn_name].trading_fee)
                for tkn_name in state.whitelisted_tokens
            ]
        )

    def get_random_trading_fee(self, trading_fee: Decimal) -> Decimal:
        min_trading_fee, max_trading_fee = max(
            trading_fee / Decimal("3"), Decimal("0.001")
        ), min(trading_fee * Decimal("3"), Decimal("0.05"))
        return Decimal(
            self.random.uniform(float(min_trading_fee), float(max_trading_fee))
        )

    def get_random_network_fee(self, network_fee: Decimal) -> Decimal:
        min_fee, max_fee = max(network_fee / Decimal("2"), Decimal("0.05")), min(
            network_fee * Decimal("2"), Decimal("0.25")
        )
        return Decimal(self.random.uniform(float(min_fee), float(max_fee)))

    def get_random_withdrawal_fee(self, withdrawal_fee: Decimal) -> Decimal:
        min_fee, max_fee = max(withdrawal_fee / Decimal("2"), Decimal("0.001")), min(
            withdrawal_fee * Decimal("2"), Decimal("0.01")
        )
        return Decimal(self.random.uniform(float(min_fee), float(max_fee)))

    def get_random_bnt_funding_limit(self, bnt_funding_amt: Decimal) -> Decimal:
        min_bnt_funding_limit = bnt_funding_amt * Decimal("1.5")
        max_bnt_funding_limit = bnt_funding_amt * Decimal("3.0")
        bnt_funding_limit = Decimal(
            self.random.uniform(
                float(min_bnt_funding_limit), float(max_bnt_funding_limit)
            )
        )
        return bnt_funding_limit

    def set_random_trading_fee(self):
        state = self.protocol.global_state
        for i in range(self.random.randint(1, 3)):
            tkn_name = self.random.choice([tkn for tkn in state.whitelisted_tokens])
            trading_fee = get_trading_fee(state, tkn_name)
            trading_fee = self.get_random_trading_fee(trading_fee)
            state.set_trading_fee(tkn_name, trading_fee)
            self.protocol.set_state(state)
        return self

    def set_random_network_fee(self):
        state = self.protocol.global_state
        tkn_name = self.random.choice([tkn for tkn in state.whitelisted_tokens])
        network_fee = get_network_fee(state, tkn_name)
        network_fee = self.get_random_network_fee(network_fee)
        state.set_network_fee(tkn_name, network_fee)
        self.protocol.set_state(state)
        return self

    def set_random_withdrawal_fee(self):
        state = self.protocol.global_state
        withdrawal_fee = state.withdrawal_fee
        tkn_name = self.random.choice([tkn for tkn in state.whitelisted_tokens])
        withdrawal_fee = self.get_random_withdrawal_fee(withdrawal_fee)
        state.set_withdrawal_fee(tkn_name, withdrawal_fee)
        self.protocol.set_state(state)
        return self

    def set_random_bnt_funding_limit(self):
        state = self.protocol.global_state
        tkn_name = self.random.choice([tkn for tkn in state.whitelisted_tokens])
        bnt_funding_limit = get_bnt_funding_limit(state, tkn_name)
        updated_bnt_funding_limit = self.get_random_bnt_funding_limit(bnt_funding_limit)
        state.set_bnt_funding_limit(tkn_name, updated_bnt_funding_limit)
        self.protocol.set_state(state)
        return self

    def perform_random_enable_trading(self):
        state = self.protocol.global_state
        for tkn in [tkn for tkn in state.whitelisted_tokens]:
            self.protocol.enable_trading(tkn)
        return self

    def get_random_withdrawal_amt(self, tkn_name: str) -> Decimal:
        user_balance = get_user_balance(
            self.protocol.global_state, self.user_name, tkn_name
        )
        return user_balance * Decimal(self.random.uniform(float(0.001), float(0.5)))

    def get_random_cooldown_amt(self, user_bntkn_amt: Decimal) -> Decimal:
        max_amt, min_amt = user_bntkn_amt * Decimal(
            "0.01"
        ), user_bntkn_amt * Decimal("0.001")
        return Decimal(self.random.uniform(float(min_amt), float(max_amt)))

    def is_protocol_bnbnt_healthy(
            self, protocol_bnbnt: Decimal, bnbnt_supply: Decimal
    ) -> bool:
        """
        Checks if the protocol owned bnbnt is at a healthy level (greater than 50%)
        """
        return protocol_bnbnt / bnbnt_supply > Decimal("0.5")

    def get_deposit_payload(
            self, state: State
    ) -> Tuple[str, str, Decimal, Decimal, Decimal, Decimal, Decimal]:
        """
        Gets the input data required for a deposit.
        """
        user_name = self.user_name
        tkn_name, target_tkn = self.get_random_tkn_names(state)
        user_tkn = get_user_balance(state, user_name, tkn_name)
        user_bnt = get_user_balance(state, user_name, "bnt")
        bnbnt_supply = get_pooltoken_balance(state, "bnt")
        protocol_bnbnt = get_protocol_wallet_balance(state, "bnt")
        bnbnt_rate = get_bnbnt_rate(state)
        return (
            user_name,
            tkn_name,
            user_tkn,
            user_bnt,
            bnbnt_supply,
            protocol_bnbnt,
            bnbnt_rate,
        )

    def random_distribute_autocompounding_program(self):
        """
        Performs a random trade on the server.
        """
        state = self.protocol.global_state
        timestamp = self.timestamp * 100000
        for tkn_name in state.whitelisted_tokens:
            if tkn_name in state.active_autocompounding_programs:
                self.protocol.distribute_autocompounding_program(
                    tkn_name=tkn_name, timestamp=timestamp
                )

    def create_random_autocompounding_rewards(self):
        """
        Performs a random trade on the server.
        """
        state = self.protocol.global_state
        timestamp = self.timestamp
        start_time = 1 + timestamp
        tkn_name = self.random.choice([tkn for tkn in state.whitelisted_tokens])
        distribution_type = self.random.choice(["flat", "exp"])
        if distribution_type == "flat":
            self.protocol.create_autocompounding_program(
                state=state,
                tkn_name=tkn_name,
                distribution_type=distribution_type,
                total_rewards="86400",
                total_duration_in_days=365,
                start_time=start_time,
                timestamp=timestamp,
            )
        else:
            self.protocol.create_autocompounding_program(
                state=state,
                tkn_name=tkn_name,
                distribution_type=distribution_type,
                half_life_days=1,
                total_rewards="360000",
                start_time=start_time,
                timestamp=timestamp,
            )

    def perform_random_begin_cooldown(self):
        """
        Begins a random cooldown.
        """
        state = self.protocol.global_state
        timestamp = self.timestamp
        for i in range(self.random.randint(1, 10)):
            user_name = self.user_name
            tkn_name, target_tkn = self.get_random_tkn_names(state)
            user_bntkn_amt = get_user_balance(state, user_name, tkn_name)
            bntkn_rate = compute_bntkn_rate(state, tkn_name)
            if pd.isnull(bntkn_rate):
                bntkn_rate = Decimal("0")
            if pd.isnull(user_bntkn_amt):
                user_bntkn_amt = Decimal("0")
            if user_bntkn_amt > 0 and bntkn_rate > 0:
                bntkn_amt = self.get_random_cooldown_amt(user_bntkn_amt)
                withdraw_value = bntkn_amt / bntkn_rate
                self.protocol.begin_cooldown(
                    tkn_name=tkn_name,
                    tkn_amt=withdraw_value,
                    user_name=user_name,
                    timestamp=timestamp,
                )
        return self

    def perform_random_deposit(self):
        """
        Performs a random deposit action
        """
        target_tvl = self.target_tvl
        state = self.protocol.global_state
        timestamp = self.timestamp
        (
            user_name,
            tkn_name,
            user_tkn,
            user_bnt,
            bnbnt_supply,
            protocol_bnbnt,
            bnbnt_rate,
        ) = self.get_deposit_payload(state)
        deposit_amt = None
        if tkn_name != "bnt":
            vault_balance = get_vault_balance(state, tkn_name)
            token_price, bnt_price = get_prices(state, tkn_name)
            vault_tvl = compute_vault_tkn_tvl(vault_balance, token_price)
            if vault_tvl < target_tvl:
                max_tkn_deposit = compute_max_tkn_deposit(
                    vault_tvl, target_tvl, user_tkn
                )
                deposit_amt = self.get_random_amt(max_tkn_deposit)
                if pd.isnull(deposit_amt):
                    deposit_amt = Decimal('0')
                if pd.isnull(user_tkn):
                    user_tkn = Decimal('0')
                if 0 < deposit_amt < user_tkn:
                    self.protocol.deposit(
                        tkn_name,
                        deposit_amt,
                        user_name,
                        timestamp,
                    )
        elif tkn_name == "bnt":
            if bnbnt_supply > 0 and self.is_protocol_bnbnt_healthy(
                    protocol_bnbnt, bnbnt_supply
            ):
                max_bnt_deposit = get_max_bnt_deposit(
                    state, user_bnt
                )
                deposit_amt = self.get_random_amt(max_bnt_deposit)

                if pd.isnull(deposit_amt):
                    deposit_amt = Decimal('0')
                if pd.isnull(user_tkn):
                    user_tkn = Decimal('0')

                if 0 < deposit_amt < user_tkn:
                    self.protocol.deposit(
                        tkn_name, deposit_amt, user_name, timestamp
                    )
        self.latest_tkn_name = tkn_name
        self.latest_amt = deposit_amt
        return self

    def process_withdrawal(
            self,
            user_name: str,
            id_number: int,
            timestamp: int = 0,
    ):
        """
        Main withdrawal logic based on the withdraw algorithm of the BIP15 spec.
        """
        state = self.protocol.global_state

        (
            id_number,
            cooldown_timestamp,
            tkn_name,
            pool_token_amt,
            withdraw_value,
            user_name,
        ) = unpack_withdrawal_cooldown(state, user_name, id_number)

        cooldown_time = state.cooldown_time
        cool_down_complete = timestamp - cooldown_timestamp >= cooldown_time
        if cool_down_complete:
            self.protocol.withdraw(
                user_name=user_name,
                id_number=id_number,
                timestamp=timestamp,
                tkn_name=tkn_name,
                tkn_amt=withdraw_value,
            )
        self.latest_tkn_name = tkn_name
        self.latest_amt = withdraw_value
        return self

    def perform_random_withdrawal(self):
        """
        Perform random withdraw action.
        """
        state = self.protocol.global_state
        timestamp = self.timestamp
        user_name = self.random.choice(state.usernames)
        tkn_name, target_tkn = self.get_random_tkn_names(state)
        pending_withdrawals = get_user_pending_withdrawals(state, user_name, tkn_name)
        if len(pending_withdrawals) > 0:
            id_number = self.random.choice(pending_withdrawals)
            self.process_withdrawal(
                user_name=user_name, id_number=id_number, timestamp=timestamp
            )
        return self

    def perform_random_vortex_burner(self):
        """
        Simulation purposes only.
        """
        state = self.protocol.global_state
        vortex_burner(state, self.user_name)
        return self

    def transform_results(self, results: pd.DataFrame, simulation_tokens: list) -> pd.DataFrame:
        nl = []
        results_list = [results[['level_2', 'timestamp', tkn]] for tkn in simulation_tokens]
        state = self.protocol.global_state
        for df in results_list:
            tkn_name = df.columns[-1]
            df['tkn_name'] = [tkn_name for _ in range(len(df))]
            df = df.rename({tkn_name: 'amount', 'level_2': 'name'}, axis=1)
            df = df.sort_values(['tkn_name', 'timestamp', 'name'])
            df = df[['timestamp', 'tkn_name', 'name', 'amount']]
            nl.append(df)
        return pd.concat(nl)

    def reduce_trading_liquidity(self, n_periods, constant_multiplier):
        from statistics import mean
        state = self.protocol.global_state
        for tkn_name in list(state.whitelisted_tokens):
            try:
                new_bnt_funding_limit = mean(self.rolling_trade_fees[tkn_name][-n_periods:]) * constant_multiplier
                """
                Updates the state of the appropriate pool, and the protocol holdings, as required.
                """
                current_bnt_funding_limit = get_bnt_funding_limit(state, tkn_name)
                if round(float(current_bnt_funding_limit), 5) != round(float(new_bnt_funding_limit),5):
                    updated_bnt_trading_liquidity = Decimal(new_bnt_funding_limit)
                    bnt_trading_liquidity = get_bnt_trading_liquidity(state, tkn_name)

                    tkn_trading_liquidity = get_tkn_trading_liquidity(state, tkn_name)
                    ema_rate = get_ema_rate(state, tkn_name)
                    bnt_renounced = bnt_trading_liquidity - updated_bnt_trading_liquidity
                    updated_tkn_trading_liquidity = max(tkn_trading_liquidity - bnt_renounced / ema_rate, 0)

                    if get_is_price_stable(state, tkn_name):
                        print('bnt_funding_limit', tkn_name, current_bnt_funding_limit, ' --> ', new_bnt_funding_limit)
                        state.decrease_bnt_trading_liquidity(tkn_name, bnt_renounced)
                        state.decrease_staked_balance(tkn_name, bnt_renounced)
                        state.decrease_vault_balance(tkn_name, bnt_renounced)
                        state.decrease_pooltoken_balance(tkn_name, bnt_renounced)
                        state.decrease_protocol_wallet_balance(tkn_name, bnt_renounced)
                        state.set_bnt_funding_limit(tkn_name, updated_bnt_trading_liquidity)
                        state.set_bnt_funding_amt(tkn_name, updated_bnt_trading_liquidity)
                        state.set_tkn_trading_liquidity(tkn_name, updated_tkn_trading_liquidity)
                        if check_pool_shutdown(state, tkn_name):
                            state = shutdown_pool(state, tkn_name)
                        self.protocol.set_state(state)
            except:
                pass
            
    def run(self, transact, mean_events_per_day=None, n_periods=None, constant_multiplier=None, is_proposal=False):
        for ct in range(self.num_timesteps):
            self.timestamp = ct
            transact(self, is_proposal)
            if is_proposal:
                try:
                    ts_compare = (num_timestamps_per_day / mean_events_per_day) * n_periods
                    if self.timestamp > ts_compare:
                        self.reduce_trading_liquidity(
                            int(round(mean_events_per_day * n_periods, 0)), constant_multiplier)
                except:
                    pass
        return pd.concat(self.logger)


Load the `MonteCarloGenerator` class parameters:

In [0]:
simulator = MonteCarloGenerator(
    target_tvl=target_tvl,
    whitelisted_tokens= whitelisted_tokens,
    price_feed=price_feeds,
    user_initial_balances=user_initial_balances,
    simulation_actions_count=simulation_actions_count,
    num_timesteps=num_timesteps,
    pool_freq_dist=pool_freq_dist,
    action_freq_dist=action_freq_dist,
    bnt_min_liquidity=bnt_min_liquidity
)

Run the baseline simulation:

In [0]:
baseline_output = simulator.run(transact)
baseline_output

eth pool is shutting down 136
link pool is shutting down 198
eth pool is shutting down 262
eth pool is shutting down 308
link pool is shutting down 386
link pool is shutting down 496
link pool is shutting down 575
link pool is shutting down 804
link pool is shutting down 857
link pool is shutting down 1007
link pool is shutting down 1218
dai pool is shutting down 1288
link pool is shutting down 1360
dai pool is shutting down 1733
Out[21]:

timestamp 
 latest_action 
 latest_amt 
 latest_tkn_name 
 eth_bnt_funding_limit 
 eth_vault 
 eth_staking 
 eth_surplus 
 eth_surplus_bnt 
 eth_surplus_usd 
 eth_tkn_trading_liquidity 
 eth_bnt_trading_liquidity 
 dai_bnt_funding_limit 
 dai_vault 
 dai_staking 
 dai_surplus 
 dai_surplus_bnt 
 dai_surplus_usd 
 dai_tkn_trading_liquidity 
 dai_bnt_trading_liquidity 
 link_bnt_funding_limit 
 link_vault 
 link_staking 
 link_surplus 
 link_surplus_bnt 
 link_surplus_usd 
 link_tkn_trading_liquidity 
 link_bnt_trading_liquidity 
 bat_bnt_funding_limit 
 bat_vault 
 bat_staking 
 bat_surplus 
 bat_surplus_bnt 
 bat_surplus_usd 
 bat_tkn_trading_liquidity 
 bat_bnt_trading_liquidity 
 usdc_bnt_funding_limit 
 usdc_vault 
 usdc_staking 
 usdc_surplus 
 ... 
 mana_surplus 
 mana_surplus_bnt 
 mana_surplus_usd 
 mana_tkn_trading_liquidity 
 mana_bnt_trading_liquidity 
 mln_bnt_funding_limit 
 mln_vault 
 mln_staking 
 mln_surplus 
 mln_surplus_bnt 
 mln_surplus_usd 
 mln_tkn_trading_liquidity 
 mln_bnt_trading_liquidity 
 usdt_bnt_funding_limit 
 usdt_vault 
 usdt_staking 
 usdt_surplus 
 usdt_surplus_bnt 
 usdt_surplus_usd 
 usdt_tkn_trading_liquidity 
 usdt_bnt_trading_liquidity 
 ocean_bnt_funding_limit 
 ocean_vault 
 ocean_staking 
 ocean_surplus 
 ocean_surplus_bnt 
 ocean_surplus_usd 
 ocean_tkn_trading_liquidity 
 ocean_bnt_trading_liquidity 
 omg_bnt_funding_limit 
 omg_vault 
 omg_staking 
 omg_surplus 
 omg_surplus_bnt 
 omg_surplus_usd 
 omg_tkn_trading_liquidity 
 omg_bnt_trading_liquidity 
 total_surplus 
 total_surplus_bnt 
 total_surplus_usd 
 
 
 
 
 0 
 1 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 
 
 0 
 2 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 
 
 0 
 13 
 deposit 
 None 
 bnt 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 
 
 0 
 14 
 arbitrage_trade 
 0 
 bnt_eth 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 
 
 0 
 17 
 deposit 
 16752.190420827231719158589839935302734375 
 link 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 16752.19042082723171915858984 
 16752.19042082723171915858984 
 0E-23 
 0E-50 
 0E-103 
 6985.357466063348139810621779 
 40000 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0E-23 
 0E-50 
 0E-103 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ..

In [0]:
simulator.rolling_trade_fees

Out[22]: {'eth': [Decimal('4213.087806703304177325275705'),
 Decimal('0.8756980694422897662342025191'),
 Decimal('2073.739924904980878831760681'),
 Decimal('0.3511186928709043452200886902'),
 Decimal('0.05678750696704015714382782523'),
 Decimal('1896.280932190416466105778954'),
 Decimal('4193.134640135925751424038253'),
 Decimal('0.8775718335950685235164316920'),
 Decimal('51.49864843169693192206719967'),
 Decimal('0.0008196660146369457625022197900'),
 Decimal('0.2054317131681950824500508899'),
 Decimal('0.0002120694883052175246099170951'),
 Decimal('138.0962986426470832949536075'),
 Decimal('0.04865912007424876264189314816'),
 Decimal('0.00004922123855290852506019165217'),
 Decimal('0.2747878767218996566058525124'),
 Decimal('148.5734523311158757241015516'),
 Decimal('0.0003043711364228111514603750296'),
 Decimal('0.04653656417470991469136616195'),
 Decimal('0.005844889421443834026109254617'),
 Decimal('0.04133346762510618040839339432'),
 Decimal('0.001003640328121559129784906264'),
 Decimal('8.062832587426276706689953986'),
 Decimal('63.11398383581352160457852739'),
 Decimal('0.2025044101818248930555973138'),
 Decimal('104.2622846884011902167887811'),
 Decimal('0.06200477830764646739364047214'),
 Decimal('0.08193668144215960882123222046'),
 Decimal('31.36985889747590838592284562'),
 Decimal('0.05554851194224170895221504228'),
 Decimal('58.86266398357573156060614628'),
 Decimal('0.05592576346902366413042359135'),
 Decimal('0.09103515994092248318257821744'),
 Decimal('0.05887585685164150422895379586'),
 Decimal('0.01841823928568103889807428292'),
 Decimal('77.93413712539928060035386100'),
 Decimal('26.78335852086881823257639478'),
 Decimal('0.1594509693065633213889143120'),
 Decimal('0.002218538156830375136635483591'),
 Decimal('0.01265374474497578471637734002'),
 Decimal('30.45673288473559059650132873'),
 Decimal('0.01192071435208880185466944258'),
 Decimal('66.03381717854344652392069117'),
 Decimal('0.1731220303307960218505418838'),
 Decimal('63.37336680393359461190375726'),
 Decimal('0.06161526944435377842319145569'),
 Decimal('0.04125047209613327214111992625'),
 Decimal('66.85315862421172868969382062'),
 Decimal('0.03765625234370314102400586065'),
 Decimal('0.0009788666480096675464582187188'),
 Decimal('0.04742470836414692370605403632'),
 Decimal('0.05318607696299693614303643484'),
 Decimal('0.02504520328374164678848571550'),
 Decimal('0.2329188235898654673606654484'),
 Decimal('72.49451677896733559985761820'),
 Decimal('21.26879779007999087026781398'),
 Decimal('11.67206718093999056965708951'),
 Decimal('0.03779462222054034263713222457'),
 Decimal('0.04023835227459848340458847815'),
 Decimal('0.05818973124836285502425885372'),
 Decimal('66.32629489142532417301590825'),
 Decimal('0.1433787012358225671350761450'),
 Decimal('0.5056212535080354607808333559'),
 Decimal('18.83449075135982895584409893'),
 Decimal('0.02636872519794390703448713484'),
 Decimal('44.73482443090864687480373221'),
 Decimal('19.23026212691291627655924793'),
 Decimal('0.04925143630451992837256687010'),
 Decimal('0.00004981840267891903218628371499'),
 Decimal('0.2372983545727054277563183859'),
 Decimal('0.08610816991839937829308235300'),
 Decimal('44.94059143726599310439006005'),
 Decimal('0.04421606838968936610243773874'),
 Decimal('0.09519568063732960693446780218'),
 Decimal('39.50268352080227564288896862'),
 Decimal('27.76384872817769936073484120'),
 Decimal('0.04062985863831674199089759912'),
 Decimal('25.15275785627261554659216736'),
 Decimal('0.004790182006858116269670118513'),
 Decimal('0.08882268382051717570581784508'),
 Decimal('0.1984112912224780345127328474'),
 Decimal('0.3661748589348795235309808049'),
 Decimal('67.39935515193697872792150075'),
 Decimal('0.1231041150720201346479423343'),
 Decimal('0.05333878822324174039841245229'),
 Decimal('74.88238683258059729690827675'),
 Decimal('0.02001861515154909345353176513'),
 Decimal('8.051083539062330352200882584'),
 Decimal('0.1115121051279949252197959785'),
 Decimal('0.0015095500529414653311313447

Run the simulation using the proposal's modified parameters:

In [0]:
simulator = MonteCarloGenerator(
    target_tvl=target_tvl,
    whitelisted_tokens= whitelisted_tokens,
    price_feed=price_feeds,
    user_initial_balances=user_initial_balances,
    simulation_actions_count=simulation_actions_count,
    num_timesteps=num_timesteps,
    pool_freq_dist=pool_freq_dist,
    action_freq_dist=action_freq_dist,
    bnt_min_liquidity=bnt_min_liquidity
)

Note below that the `simulator.run(...)` parameters are significantly different from the baseline simulation above.

In [0]:
proposal_output = simulator.run(transact, mean_events_per_day, n_periods, constant_multiplier, is_proposal=True)
proposal_output

eth pool is shutting down 136
bnt_funding_limit eth 1000000 --> 1095630.511240914081443792576
link pool is shutting down 198
bnt_funding_limit link 1000000 --> 45493.50792800723405769608447
link pool is shutting down 399
bnt_funding_limit link 45493.50792800723405769608447 --> 63898.71855178105556377869692
link pool is shutting down 509
bnt_funding_limit link 63898.71855178105556377869692 --> 74610.50763713076724944643561
link pool is shutting down 588
bnt_funding_limit link 74610.50763713076724944643561 --> 77233.11301258898423243772916
link pool is shutting down 817
bnt_funding_limit link 77233.11301258898423243772916 --> 79487.14110803862804672348635
link pool is shutting down 870
bnt_funding_limit link 79487.14110803862804672348635 --> 94698.58722342861924544607196
link pool is shutting down 1020
bnt_funding_limit link 94698.58722342861924544607196 --> 83478.23200916744726157330770
link pool is shutting down 1238
bnt_funding_limit link 83478.23200916744726157330770 --> 88087.88277982947888376284771
dai pool is shutting down 1308
bnt_funding_limit dai 1000000 --> 64814.23592566804785622094641
link pool is shutting down 1380
bnt_funding_limit link 88087.88277982947888376284771 --> 89712.06930369652052622122920
link pool is shutting down 1655
bnt_funding_limit link 89712.06930369652052622122920 --> 93622.63014843524002755491876
link pool is shutting down 1921
bnt_funding_limit link 93622.63014843524002755491876 --> 99802.18734988879598683461043
link pool is shutting down 2126
bnt_funding_limit link 99802.18734988879598683461043 --> 108522.2587893684651241119234
link pool is shutting down 2316
bnt_funding_limit link 108522.2587893684651241119234 --> 115004.8955882755313242939009
link pool is shutting down 2362
bnt_funding_limit link 115004.8955882755313242939009 --> 124676.0603565195518027326018
bnt_funding_limit link 124676.0603565195518027326018 --> 121776.8080122465665848693170
bnt_funding_limit link 121776.8080122465665848693170 --> 71122.53666434746937027796746
bnt_funding_limit link 71122.53666434746937027796746 --> 67047.26828524118797307187270
bnt_funding_limit link 67047.26828524118797307187270 --> 66364.96177515776511989647328
bnt_funding_limit link 66364.96177515776511989647328 --> 65663.04497965772802410693049
bnt_funding_limit eth 1095630.511240914081443792576 --> 403726.5359692615495347803508
bnt_funding_limit eth 403726.5359692615495347803508 --> 400404.2083299636100471922993
bnt_funding_limit link 65663.04497965772802410693049 --> 64612.96461514797095989757224
bnt_funding_limit eth 400404.2083299636100471922993 --> 405583.2384214999033323705301
bnt_funding_limit eth 405583.2384214999033323705301 --> 485591.7167883161140804436059
bnt_funding_limit eth 485591.7167883161140804436059 --> 488763.7166691692091883034961
bnt_funding_limit eth 488763.7166691692091883034961 --> 484915.3624130838709857241333
bnt_funding_limit link 64612.96461514797095989757224 --> 63949.92390480824638585682852
bnt_funding_limit eth 484915.3624130838709857241333 --> 573855.3390514022077018882512
bnt_funding_limit eth 573855.3390514022077018882512 --> 611458.0201329184476782792413
bnt_funding_limit eth 611458.0201329184476782792413 --> 606719.3841061033084727442361
bnt_funding_limit link 63949.92390480824638585682852 --> 63297.95998396686307320265632
bnt_funding_limit eth 606719.3841061033084727442361 --> 609968.6526958824936813639264
bnt_funding_limit link 63297.95998396686307320265632 --> 61435.07602511886664303209106
bnt_funding_limit eth 609968.6526958824936813639264 --> 720014.9417072858889853623452
bnt_funding_limit eth 720014.9417072858889853623452 --> 784721.6719435415587771550793
bnt_funding_limit eth 784721.6719435415587771550793 --> 778996.5731564291493728163295
bnt_funding_limit eth 778996.5731564291493728163295 --> 847712.5318446346699258496331
bnt_funding_limit eth 847712.5318446346699258496331 --> 931763.4298629380847981519111
bnt_funding_limit link 61435.07602511886664303209106 --> 60348.46657288037871365119249
bnt_funding_l

timestamp 
 latest_action 
 latest_amt 
 latest_tkn_name 
 eth_bnt_funding_limit 
 eth_vault 
 eth_staking 
 eth_surplus 
 eth_surplus_bnt 
 eth_surplus_usd 
 eth_tkn_trading_liquidity 
 eth_bnt_trading_liquidity 
 dai_bnt_funding_limit 
 dai_vault 
 dai_staking 
 dai_surplus 
 dai_surplus_bnt 
 dai_surplus_usd 
 dai_tkn_trading_liquidity 
 dai_bnt_trading_liquidity 
 link_bnt_funding_limit 
 link_vault 
 link_staking 
 link_surplus 
 link_surplus_bnt 
 link_surplus_usd 
 link_tkn_trading_liquidity 
 link_bnt_trading_liquidity 
 bat_bnt_funding_limit 
 bat_vault 
 bat_staking 
 bat_surplus 
 bat_surplus_bnt 
 bat_surplus_usd 
 bat_tkn_trading_liquidity 
 bat_bnt_trading_liquidity 
 usdc_bnt_funding_limit 
 usdc_vault 
 usdc_staking 
 usdc_surplus 
 ... 
 mana_surplus 
 mana_surplus_bnt 
 mana_surplus_usd 
 mana_tkn_trading_liquidity 
 mana_bnt_trading_liquidity 
 mln_bnt_funding_limit 
 mln_vault 
 mln_staking 
 mln_surplus 
 mln_surplus_bnt 
 mln_surplus_usd 
 mln_tkn_trading_liquidity 
 mln_bnt_trading_liquidity 
 usdt_bnt_funding_limit 
 usdt_vault 
 usdt_staking 
 usdt_surplus 
 usdt_surplus_bnt 
 usdt_surplus_usd 
 usdt_tkn_trading_liquidity 
 usdt_bnt_trading_liquidity 
 ocean_bnt_funding_limit 
 ocean_vault 
 ocean_staking 
 ocean_surplus 
 ocean_surplus_bnt 
 ocean_surplus_usd 
 ocean_tkn_trading_liquidity 
 ocean_bnt_trading_liquidity 
 omg_bnt_funding_limit 
 omg_vault 
 omg_staking 
 omg_surplus 
 omg_surplus_bnt 
 omg_surplus_usd 
 omg_tkn_trading_liquidity 
 omg_bnt_trading_liquidity 
 total_surplus 
 total_surplus_bnt 
 total_surplus_usd 
 
 
 
 
 0 
 1 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 
 
 0 
 2 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 
 
 0 
 13 
 deposit 
 None 
 bnt 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 
 
 0 
 14 
 arbitrage_trade 
 0 
 bnt_eth 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 
 
 0 
 17 
 deposit 
 16752.190420827231719158589839935302734375 
 link 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 16752.19042082723171915858984 
 16752.19042082723171915858984 
 0E-23 
 0E-50 
 0E-103 
 6985.357466063348139810621779 
 40000 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0E-23 
 0E-50 
 0E-103 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ..

In [0]:
# len(simulator.rolling_trade_fees['eth'])

Combine the results to compare side-by-side:

In [0]:
proposal_output['type'] = ['proposal' for _ in range(len(proposal_output))]
baseline_output['type'] = ['baseline' for _ in range(len(baseline_output))]
combined = pd.concat([proposal_output, baseline_output])
combined

Out[26]:

timestamp 
 latest_action 
 latest_amt 
 latest_tkn_name 
 eth_bnt_funding_limit 
 eth_vault 
 eth_staking 
 eth_surplus 
 eth_surplus_bnt 
 eth_surplus_usd 
 eth_tkn_trading_liquidity 
 eth_bnt_trading_liquidity 
 dai_bnt_funding_limit 
 dai_vault 
 dai_staking 
 dai_surplus 
 dai_surplus_bnt 
 dai_surplus_usd 
 dai_tkn_trading_liquidity 
 dai_bnt_trading_liquidity 
 link_bnt_funding_limit 
 link_vault 
 link_staking 
 link_surplus 
 link_surplus_bnt 
 link_surplus_usd 
 link_tkn_trading_liquidity 
 link_bnt_trading_liquidity 
 bat_bnt_funding_limit 
 bat_vault 
 bat_staking 
 bat_surplus 
 bat_surplus_bnt 
 bat_surplus_usd 
 bat_tkn_trading_liquidity 
 bat_bnt_trading_liquidity 
 usdc_bnt_funding_limit 
 usdc_vault 
 usdc_staking 
 usdc_surplus 
 ... 
 mana_surplus_bnt 
 mana_surplus_usd 
 mana_tkn_trading_liquidity 
 mana_bnt_trading_liquidity 
 mln_bnt_funding_limit 
 mln_vault 
 mln_staking 
 mln_surplus 
 mln_surplus_bnt 
 mln_surplus_usd 
 mln_tkn_trading_liquidity 
 mln_bnt_trading_liquidity 
 usdt_bnt_funding_limit 
 usdt_vault 
 usdt_staking 
 usdt_surplus 
 usdt_surplus_bnt 
 usdt_surplus_usd 
 usdt_tkn_trading_liquidity 
 usdt_bnt_trading_liquidity 
 ocean_bnt_funding_limit 
 ocean_vault 
 ocean_staking 
 ocean_surplus 
 ocean_surplus_bnt 
 ocean_surplus_usd 
 ocean_tkn_trading_liquidity 
 ocean_bnt_trading_liquidity 
 omg_bnt_funding_limit 
 omg_vault 
 omg_staking 
 omg_surplus 
 omg_surplus_bnt 
 omg_surplus_usd 
 omg_tkn_trading_liquidity 
 omg_bnt_trading_liquidity 
 total_surplus 
 total_surplus_bnt 
 total_surplus_usd 
 type 
 
 
 
 
 0 
 1 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 proposal 
 
 
 0 
 2 
 cooldown 
 None 
 None 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-54 
 0 
 0 
 0 
 0 
 0E-54 
 proposal 
 
 
 0 
 13 
 deposit 
 None 
 bnt 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 proposal 
 
 
 0 
 14 
 arbitrage_trade 
 0 
 bnt_eth 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0 
 0 
 0E-53 
 proposal 
 
 
 0 
 17 
 deposit 
 16752.190420827231719158589839935302734375 
 link 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 16752.19042082723171915858984 
 16752.19042082723171915858984 
 0E-23 
 0E-50 
 0E-103 
 6985.357466063348139810621779 
 40000 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 ... 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 1000000 
 0 
 0 
 0 
 0 
 0E-53 
 0 
 0 
 0E-23 
 0E-50 
 0E-103 
 proposal 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 


Print the list of data points we collected for each time step.

In [0]:
print(list(combined.columns))

['timestamp', 'latest_action', 'latest_amt', 'latest_tkn_name', 'eth_bnt_funding_limit', 'eth_vault', 'eth_staking', 'eth_surplus', 'eth_surplus_bnt', 'eth_surplus_usd', 'eth_tkn_trading_liquidity', 'eth_bnt_trading_liquidity', 'dai_bnt_funding_limit', 'dai_vault', 'dai_staking', 'dai_surplus', 'dai_surplus_bnt', 'dai_surplus_usd', 'dai_tkn_trading_liquidity', 'dai_bnt_trading_liquidity', 'link_bnt_funding_limit', 'link_vault', 'link_staking', 'link_surplus', 'link_surplus_bnt', 'link_surplus_usd', 'link_tkn_trading_liquidity', 'link_bnt_trading_liquidity', 'bat_bnt_funding_limit', 'bat_vault', 'bat_staking', 'bat_surplus', 'bat_surplus_bnt', 'bat_surplus_usd', 'bat_tkn_trading_liquidity', 'bat_bnt_trading_liquidity', 'usdc_bnt_funding_limit', 'usdc_vault', 'usdc_staking', 'usdc_surplus', 'usdc_surplus_bnt', 'usdc_surplus_usd', 'usdc_tkn_trading_liquidity', 'usdc_bnt_trading_liquidity', 'ren_bnt_funding_limit', 'ren_vault', 'ren_staking', 'ren_surplus', 'ren_surplus_bnt', 'ren_surplus_usd', 'ren_tkn_trading_liquidity', 'ren_bnt_trading_liquidity', 'wbtc_bnt_funding_limit', 'wbtc_vault', 'wbtc_staking', 'wbtc_surplus', 'wbtc_surplus_bnt', 'wbtc_surplus_usd', 'wbtc_tkn_trading_liquidity', 'wbtc_bnt_trading_liquidity', 'enj_bnt_funding_limit', 'enj_vault', 'enj_staking', 'enj_surplus', 'enj_surplus_bnt', 'enj_surplus_usd', 'enj_tkn_trading_liquidity', 'enj_bnt_trading_liquidity', 'mkr_bnt_funding_limit', 'mkr_vault', 'mkr_staking', 'mkr_surplus', 'mkr_surplus_bnt', 'mkr_surplus_usd', 'mkr_tkn_trading_liquidity', 'mkr_bnt_trading_liquidity', 'matic_bnt_funding_limit', 'matic_vault', 'matic_staking', 'matic_surplus', 'matic_surplus_bnt', 'matic_surplus_usd', 'matic_tkn_trading_liquidity', 'matic_bnt_trading_liquidity', 'mana_bnt_funding_limit', 'mana_vault', 'mana_staking', 'mana_surplus', 'mana_surplus_bnt', 'mana_surplus_usd', 'mana_tkn_trading_liquidity', 'mana_bnt_trading_liquidity', 'mln_bnt_funding_limit', 'mln_vault', 'mln_staking', 'mln_surplus', 'mln_surplus_bnt', 'mln_surplus_usd', 'mln_tkn_trading_liquidity', 'mln_bnt_trading_liquidity', 'usdt_bnt_funding_limit', 'usdt_vault', 'usdt_staking', 'usdt_surplus', 'usdt_surplus_bnt', 'usdt_surplus_usd', 'usdt_tkn_trading_liquidity', 'usdt_bnt_trading_liquidity', 'ocean_bnt_funding_limit', 'ocean_vault', 'ocean_staking', 'ocean_surplus', 'ocean_surplus_bnt', 'ocean_surplus_usd', 'ocean_tkn_trading_liquidity', 'ocean_bnt_trading_liquidity', 'omg_bnt_funding_limit', 'omg_vault', 'omg_staking', 'omg_surplus', 'omg_surplus_bnt', 'omg_surplus_usd', 'omg_tkn_trading_liquidity', 'omg_bnt_trading_liquidity', 'total_surplus', 'total_surplus_bnt', 'total_surplus_usd', 'type']

## Data visualisation

We  will start by visualising the two simulation results.

In [0]:
fig = px.line(combined, x = "timestamp", y = ['eth_bnt_funding_limit'],
              color = "type",
              title='ETH bnt funding limit')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = ['link_bnt_funding_limit'],
              color = "type",
              title='LINK bnt funding limit')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = ['eth_bnt_trading_liquidity'],
              color = "type",
              title='ETH bnt trading liquidity')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = ['link_bnt_trading_liquidity'],
              color = "type",
              title='LINK bnt trading liquidity')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = 'eth_surplus',
              color='type',
               title='ETH surplus')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = 'link_surplus',
              color='type',
               title='LINK surplus')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = 'total_surplus',
              color='type',
               title='total surplus')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = 'total_surplus_bnt',
              color='type',
               title='total surplus (bnt)')
fig.show()

In [0]:
fig = px.line(combined, x = "timestamp", y = 'total_surplus_usd',
              color='type',
               title='total surplus (usd)')
fig.show()

## Optimizing the parameters

We hypothesized before that ...

We can check how the results would be if ...

## Summary

...

In [0]:
combined.to_csv('/dbfs/FileStore/tables/research/limit_max_on_curve_liquidity_results_cp.csv')

## Profiling the Results

This notebook performs exploratory data analysis (EDA) on the results dataset.

To expand on the analysis, edit [the options of pandas-profiling](https://pandas-profiling.github.io/pandas-profiling/docs/master/rtd/pages/advanced_usage.html), and rerun it.

In [0]:
keep_cols = ['timestamp','type','latest_action','latest_amt','latest_tkn_name','total_surplus','total_surplus_bnt','total_surplus_usd']
for col in combined.columns:
    if 'link' in col:
        keep_cols.append(col)
    if 'eth' in col:
        keep_cols.append(col)
    if 'dai' in col:
        keep_cols.append(col)
    try:
        combined[col] = round(combined[col].astype(float), 4)
    except: 
        pass
    
combined = combined[keep_cols]
combined

Out[38]:

timestamp 
 type 
 latest_action 
 latest_amt 
 latest_tkn_name 
 total_surplus 
 total_surplus_bnt 
 total_surplus_usd 
 eth_bnt_funding_limit 
 eth_vault 
 eth_staking 
 eth_surplus 
 eth_surplus_bnt 
 eth_surplus_usd 
 eth_tkn_trading_liquidity 
 eth_bnt_trading_liquidity 
 dai_bnt_funding_limit 
 dai_vault 
 dai_staking 
 dai_surplus 
 dai_surplus_bnt 
 dai_surplus_usd 
 dai_tkn_trading_liquidity 
 dai_bnt_trading_liquidity 
 link_bnt_funding_limit 
 link_vault 
 link_staking 
 link_surplus 
 link_surplus_bnt 
 link_surplus_usd 
 link_tkn_trading_liquidity 
 link_bnt_trading_liquidity 
 
 
 
 
 0 
 1.0 
 proposal 
 cooldown 
 NaN 
 None 
 0.000000e+00 
 0.000000e+00 
 0.000000e+00 
 1000000.0 
 0.000000e+00 
 0.0000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.00 
 0.0000 
 1000000.0 
 0.000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000 
 0.0000 
 1000000.0 
 0.000000e+00 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000000e+00 
 0.0000 
 
 
 0 
 2.0 
 proposal 
 cooldown 
 NaN 
 None 
 0.000000e+00 
 0.000000e+00 
 0.000000e+00 
 1000000.0 
 0.000000e+00 
 0.0000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.00 
 0.0000 
 1000000.0 
 0.000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000 
 0.0000 
 1000000.0 
 0.000000e+00 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000000e+00 
 0.0000 
 
 
 0 
 13.0 
 proposal 
 deposit 
 NaN 
 bnt 
 0.000000e+00 
 0.000000e+00 
 0.000000e+00 
 1000000.0 
 0.000000e+00 
 0.0000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.00 
 0.0000 
 1000000.0 
 0.000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000 
 0.0000 
 1000000.0 
 0.000000e+00 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000000e+00 
 0.0000 
 
 
 0 
 14.0 
 proposal 
 arbitrage_trade 
 0.0000 
 bnt_eth 
 0.000000e+00 
 0.000000e+00 
 0.000000e+00 
 1000000.0 
 0.000000e+00 
 0.0000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.00 
 0.0000 
 1000000.0 
 0.000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000 
 0.0000 
 1000000.0 
 0.000000e+00 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000000e+00 
 0.0000 
 
 
 0 
 17.0 
 proposal 
 deposit 
 16752.1904 
 link 
 0.000000e+00 
 0.000000e+00 
 0.000000e+00 
 1000000.0 
 0.000000e+00 
 0.0000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.00 
 0.0000 
 1000000.0 
 0.000 
 0.000000e+00 
 0.0000 
 0.0000 
 0.0000 
 0.000 
 0.0000 
 1000000.0 
 1.675219e+04 
 1.675219e+04 
 0.0000 
 0.0000 
 0.0000 
 6.985358e+03 
 40000.0000 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 0 
 43187.0 
 baseline 
 arbitrage_trade 
 14436.6789 
 eth_bnt 
 1.175533e+07 
 1.288057e+08 
 5.042949e+07 
 1000000.0 
 1.292987e+06 
 148333.3713 
 1.144654e+06 
 2155.7179 
 843.9981 
 413208.85 
 739.4011 
 1000000.0 
 1312279.701 
 1.246387e+06 
 65892.6887 
 26238.0936 
 10272.6335 
 1243569.135 
 476735.0303 
 1000000.0 
 4.940129e+06 
 4.506842e+06 
 433286.9567 
 95018.5120 
 37201.2677 
 4.325205e+06 
 888531.2839 
 
 
 0 
 43192.0 
 baseline 
 deposit 
 NaN 
 bnt 
 1.175533e+07 
 1.288057e+08 
 5.508762e+07 
 1000000.0 
 1.292987e+06 
 148333.3713 
 1.144654e+06 
 2155.7179 
 921.9574 
 413208.85 
 739.4011 
 1000000.0 
 1312279.701 
 1.246387e+06 
 65892.6887 
 26238.0936 
 11221.5079 
 1243569.135 
 476735.0303 
 1000000.0 
 4.940129e+06 
 4.506842e+06 
 433286.9567 
 95018.5120 
 40637.5172 
 4.325205e+06 
 888531.2839 
 
 
 0 
 43193.0 
 baseline 
 arbitrage_trade 
 54326.1516 
 bnt_link 
 1.150661e+07 
 1.287512e+08 
 5.422291e+07 
 1000000.0 
 1.292987e+06 
 148333.3713 
 1.144654e+06 
 2155.7179 
 907.8698 
 413208.85 
 739.4011 
 1000000.0 
 1312279.701 
 1.246387e+06 
 65892.6887 
 26238.0936 
 11050.0419 
 1243569.135 
 476735.0303 
 1000000.0 
 4.693409e+06 
 4.508836e+06 
 184573.0189 
 40476.3018 
 17046.3921 
 4.078485e+06 
 942742.2105 
 
 
 0 
 43194.0 
 baseline 
 arbitrage_trade 
 0.0000 
 bnt_link 
 1.150661e+07 
 1.287512e+08 
 5.422291e+07 
 1000000.0 
 1.2

In [0]:
from pandas_profiling import ProfileReport
df_profile = ProfileReport(combined, title="Profiling Report", 
                           progress_bar=False, 
                           infer_dtypes=False,
                           minimal=True
                          )
profile_html = df_profile.to_html()

displayHTML(profile_html)

<!doctype html> Profiling Report Toggle navigation Profiling Report Overview Variables Overview Overview Alerts 12 Reproduction Dataset statistics Number of variables 33 Number of observations 13366 Missing cells 8083 Missing cells (%) 1.8% Total size in memory 3.4 MiB Average record size in memory 264.0 B Variable types Numeric 30 Categorical 3 Alerts df_index has constant value "0" Constant latest_tkn_name has a high cardinality: 77 distinct values High cardinality latest_amt has 5434 (40.7%) missing values Missing latest_tkn_name has 2649 (19.8%) missing values Missing latest_amt is highly skewed (γ1 = 43.22476424) Skewed df_index has 13366 (100.0%) zeros Zeros latest_amt has 2489 (18.6%) zeros Zeros dai_surplus has 252 (1.9%) zeros Zeros dai_surplus_bnt has 252 (1.9%) zeros Zeros dai_surplus_usd has 252 (1.9%) zeros Zeros dai_tkn_trading_liquidity has 182 (1.4%) zeros Zeros dai_bnt_trading_liquidity has 182 (1.4%) zeros Zeros Reproduction Analysis started 2022-08-16 19:05:29.075300 Analysis finished 2022-08-16 19:05:29.522760 Duration 0.45 seconds Software version pandas-profiling v3.1.0 Download configuration <a download=config.json href="data:text/plain;charset=utf-8,%7B%22title%22%3A%20%22Profiling%20Report%22%2C%20%22dataset%22%3A%20%7B%22description%22%3A%20%22%22%2C%20%22creator%22%3A%20%22%22%2C%20%22author%22%3A%20%22%22%2C%20%22copyright_holder%22%3A%20%22%22%2C%20%22copyright_year%22%3A%20%22%22%2C%20%22url%22%3A%20%22%22%7D%2C%20%22variables%22%3A%20%7B%22descriptions%22%3A%20%7B%7D%7D%2C%20%22infer_dtypes%22%3A%20false%2C%20%22show_variable_description%22%3A%20true%2C%20%22pool_size%22%3A%200%2C%20%22progress_bar%22%3A%20false%2C%20%22vars%22%3A%20%7B%22num%22%3A%20%7B%22quantiles%22%3A%20%5B0.05%2C%200.25%2C%200.5%2C%200.75%2C%200.95%5D%2C%20%22skewness_threshold%22%3A%2020%2C%20%22low_categorical_threshold%22%3A%205%2C%20%22chi_squared_threshold%22%3A%200.0%7D%2C%20%22cat%22%3A%20%7B%22length%22%3A%20false%2C%20%22characters%22%3A%20false%2C%20%22words%22%3A%20false%2C%20%22cardinality_threshold%22%3A%2050%2C%20%22n_obs%22%3A%205%2C%20%22chi_squared_threshold%22%3A%200.0%2C%20%22coerce_str_to_date%22%3A%20false%2C%20%22redact%22%3A%20false%2C%20%22histogram_largest%22%3A%2010%7D%2C%20%22image%22%3A%20%7B%22active%22%3A%20false%2C%20%22exif%22%3A%20false%2C%20%22hash%22%3A%20false%7D%2C%20%22bool%22%3A%20%7B%22n_obs%22%3A%203%2C%20%22mappings%22%3A%20%7B%22t%22%3A%20true%2C%20%22f%22%3A%20false%2C%20%22True%22%3A%20true%2C%20%22False%22%3A%20false%2C%20%22y%22%3A%20true%2C%20%22n%22%3A%20false%7D%7D%2C%20%22path%22%3A%20%7B%22active%22%3A%20false%7D%2C%20%22file%22%3A%20%7B%22active%22%3A%20false%7D%2C%20%22url%22%3A%20%7B%22active%22%3A%20false%7D%7D%2C%20%22sort%22%3A%20null%2C%20%22missing_diagrams%22%3A%20%7B%22bar%22%3A%20false%2C%20%22matrix%22%3A%20false%2C%20%22heatmap%22%3A%20false%2C%20%22dendrogram%22%3A%20false%7D%2C%20%22correlations%22%3A%20%7B%22pearson%22%3A%20%7B%22key%22%3A%20%22%22%2C%20%22calculate%22%3A%20false%2C%20%22warn_high_correlations%22%3A%201%2C%20%22threshold%22%3A%200.9%7D%2C%20%22spearman%22%3A%20%7B%22key%22%3A%20%22%22%2C%20%22calculate%22%3A%20false%2C%20%22warn_high_correlations%22%3A%200%2C%20%22threshold%22%3A%200.9%7D%2C%20%22kendall%22%3A%20%7B%22key%22%3A%20%22%22%2C%20%22calculate%22%3A%20false%2C%20%22warn_high_correlations%22%3A%200%2C%20%22threshold%22%3A%200.9%7D%2C%20%22phi_k%22%3A%20%7B%22key%22%3A%20%22%22%2C%20%22calculate%22%3A%20false%2C%20%22warn_high_correlations%22%3A%200%2C%20%22threshold%22%3A%200.9%7D%2C%20%22cramers%22%3A%20%7B%22key%22%3A%20%22%22%2C%20%22calculate%22%3A%20false%2C%20%22warn_high_correlations%22%3A%201%2C%20%22threshold%22%3A%200.9%7D%7D%2C%20%22interactions%22%3A%20%7B%22continuous%22%3A%20false%2C%20%22targets%22%3A%20%5B%5D%7D%2C%20%22categorical_maximum_correlation_distinct%22%3A%20100%2C%20%22memory_deep%22%3A%20false%2C%20%22plot%22%3A%20%7B%22missing%22%3A%20%7B%22force_labels%22%3A%20true%2C%20%22cmap%22%3A%20%22RdBu%22%7D%2C